# Analysis toward the file of a week

The analysis on twitter is done toward 7 sequencial days from 2020-05-07(Thursday)to 2020-05-13(Wednesday)as 7 days and they are idex with 1 to 7<br>
The file 50 to 56 correspond to the day 1 to 7

In [130]:
#import the important library
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import json as js
import ast
import folium
import re
import networkx as nx
from datetime import datetime
from branca.colormap import linear
from folium.plugins import HeatMapWithTime

In [41]:
#define the boundary for the grid
lower_left_coordinates =[-125.000000,24.000000]
upper_right_coordinates =[-66.000000,50.000000]

#define the grind with the size of m_box * n_box
m_box = 70
n_box = 35

In [42]:
#open places file of places and handle the issue of single quotes
with open(r"covid_19_tweets/places.txt", encoding="utf8") as pls_file:
    pl=[]
    line= pls_file.readlines()
    for row in range(len(line)):
        temp = ast.literal_eval(line[row])
        pl.append(temp)

    pls_df=pd.DataFrame(pl)

In [43]:
#helper function to calculate the average and apply them to all
def average(number1, number2):
    return (number1 + number2) / 2.0

#compute the average data of latitude and lontitude 
pls_df['Lontitude'] = pls_df.apply(lambda x: average (x['geo']['bbox'][0],x['geo']['bbox'][2]),axis = 1)
pls_df['Latitude'] = pls_df.apply(lambda x: average (x['geo']['bbox'][1],x['geo']['bbox'][3]),axis = 1)

#filter out the location in the geo box
pls_filter = pls_df[(pls_df['Lontitude']>=lower_left_coordinates[0])&(pls_df['Lontitude']<=upper_right_coordinates[0])&(pls_df['Latitude']>=lower_left_coordinates[1])&(pls_df['Latitude']<=upper_right_coordinates[1])]
pls_filter

full_name place_type                id country_code  \
1                    Manhattan, NY       city  01a9a39529b27f36           US   
2                 Connecticut, USA      admin  e86b380cfefcced5           US   
4                  Albuquerque, NM       city  813a485b26b8dae2           US   
5                      Kansas, USA      admin  27c45d804c777999           US   
6                       Laguna, CA       city  947299911720444c           US   
...                            ...        ...               ...          ...   
118805        Boundless Adventures        poi  0e0c90877056d000           US   
118808  Saint Philip Benizi Church        poi  105c4258a4947001           US   
118811            Joe's Crab Shack        poi  07d9dd807cc83000           US   
118813               Bubble Nation        poi  0f451500b114f000           US   
118815               UPS Air Cargo        poi  07d9f44b6f886000           US   

           country                                                geo  \
1       Etats-Unis  {'type': 'Feature', 'bbox': [-74.026675, 40.68...   
2       Etats-Unis  {'type': 'Feature', 'bbox': [-73.727776, 40.95...   
4       Etats-Unis  {'type': 'Feature', 'bbox': [-106.7916912, 35....   
5       Etats-Unis  {'type': 'Feature', 'bbox': [-102.051769, 36.9...   
6       Etats-Unis  {'type': 'Feature', 'bbox': [-121.4882357, 38....   
...            ...                                                ...   
118805  Etats-Unis  {'type': 'Feature', 'bbox': [-71.618195, 42.36...   
118808  Etats-Unis  {'type': 'Feature', 'bbox': [-117.967347939078...   
118811  Etats-Unis  {'type': 'Feature', 'bbox': [-74.1561108827591...   
118813  Etats-Unis  {'type': 'Feature', 'bbox': [-71.151844, 42.41...   
118815  Etats-Unis  {'type': 'Feature', 'bbox': [-71.0220434099819...   

                              name   Lontitude   Latitude  
1                        Manhattan  -73.968542  40.780709  
2                      Connecticut  -72.757385  41.500753  
4                      Albuquerque -106.632718  35.117003  
5                           Kansas  -98.319925  38.498196  
6                           Laguna -121.439383  38.410428  
...                            ...         ...        ...  
118805        Boundless Adventures  -71.618195  42.362573  
118808  Saint Philip Benizi Church -117.967348  33.866919  
118811            Joe's Crab Shack  -74.156111  40.839959  
118813               Bubble Nation  -71.151844  42.414717  
118815               UPS Air Cargo  -71.022043  42.394135  

[44123 rows x 9 columns]

In [44]:
#define helper function to clear the no places situation
def geo_nan(df):
    if isinstance(df.loc['geo'], float):
        return False
    if 'place_id' in df['geo']:
        return True
    return False

In [45]:
#open the data file and handle the issue of single quotes
with open(r"covid_19_tweets/corona_tweets_50_data.txt", encoding="utf8") as corona_file:
    tw=[]
    line= corona_file.readlines()
    for row in range(len(line)):
        temp = ast.literal_eval(line[row])
        tw.append(temp)
    tws_50_df=pd.DataFrame(tw)

tws_50_df['geo_nan'] = tws_50_df.apply(geo_nan, axis=1)
tws_50_df = tws_50_df[tws_50_df['geo_nan'] == True]
tws_50_df['Day'] = 1


lang                created_at                 id_x  \
0      en  2020-05-07T04:10:01.000Z  1258247691483713537   
1      en  2020-05-08T02:00:20.000Z  1258577445881614337   
2      en  2020-05-07T04:10:01.000Z  1258247692397969408   
3      en  2020-05-07T04:10:17.000Z  1258247758772703232   
4      en  2020-05-07T04:10:25.000Z  1258247792843259910   
...   ...                       ...                  ...   
7428   en  2020-05-08T03:48:06.000Z  1258604565861031936   
7429   en  2020-05-08T03:48:51.000Z  1258604752209940488   
7430   en  2020-05-08T03:49:19.000Z  1258604871491649538   
7431   en  2020-05-08T03:49:29.000Z  1258604912172294154   
7432   en  2020-05-08T03:49:41.000Z  1258604963674144768   

                                                   text  \
0                   Me Neither! https://t.co/LWXJRb5lKt   
1     Wow, thisbis the next town over from mine. htt...   
2     Can she donate plasma to Ruth Bader Ginsburg? ...   
3     Trump is scared of these facts and is totally ...   
4     @realDonaldTrump Time to Dump Fauci. Watch the...   
...                                                 ...   
7428  ➡️ no COVID 19 deaths in the last 14 days\n➡️ ...   
7429  Check them out #TorontoStrong #torontolife\n#C...   
7430  NEWS: A new #COVID19 drive-thru testing site i...   
7431  @LARSENMUFC @aveeno33700817 @StarletPatty14 @T...   
7432                   Unreal!! https://t.co/NfRAoSidwH   

                                               entities   author_id  \
0     {'urls': [{'start': 12, 'end': 35, 'url': 'htt...  1128201698   
1     {'urls': [{'start': 43, 'end': 66, 'url': 'htt...   749222396   
2     {'annotations': [{'start': 25, 'end': 43, 'pro...   104372937   
3     {'annotations': [{'start': 0, 'end': 4, 'proba...   577268396   
4     {'mentions': [{'start': 0, 'end': 16, 'usernam...  1058201006   
...                                                 ...         ...   
7428                                                NaN   363250511   
7429  {'hashtags': [{'start': 15, 'end': 29, 'tag': ...    56848957   
7430  {'hashtags': [{'start': 12, 'end': 20, 'tag': ...    52612182   
7431  {'mentions': [{'start': 0, 'end': 11, 'usernam...  1276820989   
7432  {'urls': [{'start': 9, 'end': 32, 'url': 'http...   488572353   

                   source  possibly_sensitive  \
0      Twitter for iPhone               False   
1     Twitter for Android               False   
2      Twitter for iPhone               False   
3      Twitter for iPhone               False   
4      Twitter for iPhone               False   
...                   ...                 ...   
7428   Twitter for iPhone               False   
7429  Twitter for Android               False   
7430   Twitter for iPhone               False   
7431  Twitter for Android               False   
7432   Twitter for iPhone               False   

                                         public_metrics  \
0     {'retweet_count': 0, 'reply_count': 0, 'like_c...   
1     {'retweet_count': 0, 'reply_count': 0, 'like_c...   
2     {'retweet_count': 0, 'reply_count': 0, 'like_c...   
3     {'retweet_count': 9, 'reply_count': 1, 'like_c...   
4     {'retweet_count': 0, 'reply_count': 0, 'like_c...   
...                                                 ...   
7428  {'retweet_count': 2, 'reply_count': 1, 'like_c...   
7429  {'retweet_count': 0, 'reply_count': 0, 'like_c...   
7430  {'retweet_count': 3, 'reply_count': 0, 'like_c...   
7431  {'retweet_count': 0, 'reply_count': 2, 'like_c...   
7432  {'retweet_count': 0, 'reply_count': 0, 'like_c...   

                                    context_annotations  ...  \
0     [{'domain': {'id': '65', 'name': 'Interests an...  ...   
1                                                   NaN  ...   
2     [{'domain': {'id': '123', 'name': 'Ongoing New...  ...   
3     [{'domain': {'id': '10', 'name': 'Person', 'de...  ...   
4     [{'domain': {'id': '10', 'name': 'Person', 'de...  ...   
...                                     

In [46]:
#open the data file and handle the issue of single quotes
with open(r"covid_19_tweets/corona_tweets_51_data.txt", encoding="utf8") as corona_file:
    tw=[]
    line= corona_file.readlines()
    for row in range(len(line)):
        temp = ast.literal_eval(line[row])
        tw.append(temp)
    tws_51_df=pd.DataFrame(tw)

tws_51_df['geo_nan'] = tws_51_df.apply(geo_nan, axis=1)
tws_51_df = tws_51_df[tws_51_df['geo_nan'] == True]
tws_51_df['Day'] = 2



In [47]:
#open the data file and handle the issue of single quotes
with open(r"covid_19_tweets/corona_tweets_52_data.txt", encoding="utf8") as corona_file:
    tw=[]
    line= corona_file.readlines()
    for row in range(len(line)):
        temp = ast.literal_eval(line[row])
        tw.append(temp)
    tws_52_df=pd.DataFrame(tw)
    
tws_52_df['geo_nan'] = tws_52_df.apply(geo_nan, axis=1)
tws_52_df = tws_52_df[tws_52_df['geo_nan'] == True]
tws_52_df['Day'] = 3



In [48]:
#open the data file and handle the issue of single quotes
with open(r"covid_19_tweets/corona_tweets_53_data.txt", encoding="utf8") as corona_file:
    tw=[]
    line= corona_file.readlines()
    for row in range(len(line)):
        temp = ast.literal_eval(line[row])
        tw.append(temp)
    tws_53_df=pd.DataFrame(tw)
    
tws_53_df['geo_nan'] = tws_53_df.apply(geo_nan, axis=1)
tws_53_df = tws_53_df[tws_53_df['geo_nan'] == True]
tws_53_df['Day'] = 4


In [49]:
#open the data file and handle the issue of single quotes
with open(r"covid_19_tweets/corona_tweets_54_data.txt", encoding="utf8") as corona_file:
    tw=[]
    line= corona_file.readlines()
    for row in range(len(line)):
        temp = ast.literal_eval(line[row])
        tw.append(temp)
    tws_54_df=pd.DataFrame(tw)
    
tws_54_df['geo_nan'] = tws_54_df.apply(geo_nan, axis=1)
tws_54_df = tws_54_df[tws_54_df['geo_nan'] == True]
tws_54_df['Day'] = 5


In [50]:
#open the data file and handle the issue of single quotes
with open(r"covid_19_tweets/corona_tweets_55_data.txt", encoding="utf8") as corona_file:
    tw=[]
    line= corona_file.readlines()
    for row in range(len(line)):
        temp = ast.literal_eval(line[row])
        tw.append(temp)
    tws_55_df=pd.DataFrame(tw)
    
tws_55_df['geo_nan'] = tws_55_df.apply(geo_nan, axis=1)
tws_55_df = tws_55_df[tws_55_df['geo_nan'] == True]
tws_55_df['Day'] = 6



In [53]:
#open the data file and handle the issue of single quotes
with open(r"covid_19_tweets/corona_tweets_56_data.txt", encoding="utf8") as corona_file:
    tw=[]
    line= corona_file.readlines()
    for row in range(len(line)):
        temp = ast.literal_eval(line[row])
        tw.append(temp)
    tws_56_df=pd.DataFrame(tw)
    
tws_56_df['geo_nan'] = tws_56_df.apply(geo_nan, axis=1)
tws_56_df = tws_56_df[tws_56_df['geo_nan'] == True]
tws_56_df['Day'] = 7


In [ ]:
#merge the two dataframe with the geo-id
tws_50_df['geo_id'] = tws_50_df.apply(lambda x: x['geo']['place_id'],axis = 1)
tws_50_merge = pd.merge(tws_50_df,pls_filter,how = 'inner',left_on = 'geo_id',right_on = 'id')


#merge the two dataframe with the geo-id
tws_51_df['geo_id'] = tws_51_df.apply(lambda x: x['geo']['place_id'],axis = 1)
tws_51_merge = pd.merge(tws_51_df,pls_filter,how = 'inner',left_on = 'geo_id',right_on = 'id')

#merge the two dataframe with the geo-id
tws_52_df['geo_id'] = tws_52_df.apply(lambda x: x['geo']['place_id'],axis = 1)
tws_52_merge = pd.merge(tws_52_df,pls_filter,how = 'inner',left_on = 'geo_id',right_on = 'id')

#merge the two dataframe with the geo-id
tws_53_df['geo_id'] = tws_53_df.apply(lambda x: x['geo']['place_id'],axis = 1)
tws_53_merge = pd.merge(tws_53_df,pls_filter,how = 'inner',left_on = 'geo_id',right_on = 'id')

#merge the two dataframe with the geo-id
tws_54_df['geo_id'] = tws_54_df.apply(lambda x: x['geo']['place_id'],axis = 1)
tws_54_merge = pd.merge(tws_54_df,pls_filter,how = 'inner',left_on = 'geo_id',right_on = 'id')

#merge the two dataframe with the geo-id
tws_55_df['geo_id'] = tws_55_df.apply(lambda x: x['geo']['place_id'],axis = 1)
tws_55_merge = pd.merge(tws_55_df,pls_filter,how = 'inner',left_on = 'geo_id',right_on = 'id')

#merge the two dataframe with the geo-id
tws_56_df['geo_id'] = tws_56_df.apply(lambda x: x['geo']['place_id'],axis = 1)
tws_56_merge = pd.merge(tws_56_df,pls_filter,how = 'inner',left_on = 'geo_id',right_on = 'id')

In [116]:
total_df = pd.concat([tws_50_merge, tws_51_merge,tws_52_merge,tws_53_merge,tws_54_merge,tws_55_merge,tws_56_merge])
total_df.reset_index()

index lang                created_at                 id_x  \
0          0   en  2020-05-07T04:10:01.000Z  1258247691483713537   
1          1   en  2020-05-08T02:00:20.000Z  1258577445881614337   
2          2   en  2020-05-07T04:10:01.000Z  1258247692397969408   
3          3   en  2020-05-07T04:10:17.000Z  1258247758772703232   
4          4   en  2020-05-07T04:10:25.000Z  1258247792843259910   
...      ...  ...                       ...                  ...   
47939   7207   en  2020-05-14T05:33:03.000Z  1260805303790178304   
47940   7208   en  2020-05-14T05:33:17.000Z  1260805360270573569   
47941   7209   en  2020-05-14T05:33:51.000Z  1260805502591737858   
47942   7210   en  2020-05-14T05:34:13.000Z  1260805596888039429   
47943   7211   en  2020-05-14T05:34:23.000Z  1260805638365442049   

                                                    text  \
0                    Me Neither! https://t.co/LWXJRb5lKt   
1      Wow, thisbis the next town over from mine. htt...   
2      Can she donate plasma to Ruth Bader Ginsburg? ...   
3      Trump is scared of these facts and is totally ...   
4      @realDonaldTrump Time to Dump Fauci. Watch the...   
...                                                  ...   
47939  *quits second job for more free time, reconnec...   
47940  @Lonnie68660019 @kevinjamesturma @RealLoganRya...   
47941  I like the way you think! https://t.co/5mJVVhLDop   
47942  I remember that everything Obama did was block...   
47943  🏈#DisneyMagicMoments&gt;\n@OrlandoCitySC HC #O...   

                                                entities           author_id  \
0      {'urls': [{'start': 12, 'end': 35, 'url': 'htt...          1128201698   
1      {'urls': [{'start': 43, 'end': 66, 'url': 'htt...           749222396   
2      {'annotations': [{'start': 25, 'end': 43, 'pro...           104372937   
3      {'annotations': [{'start': 0, 'end': 4, 'proba...           577268396   
4      {'mentions': [{'start': 0, 'end': 16, 'usernam...          1058201006   
...                                                  ...                 ...   
47939                                                NaN           790277215   
47940  {'mentions': [{'start': 0, 'end': 15, 'usernam...           381230743   
47941  {'urls': [{'start': 26, 'end': 49, 'url': 'htt...            29633245   
47942  {'annotations': [{'start': 27, 'end': 31, 'pro...  738848946559328258   
47943  {'hashtags': [{'start': 1, 'end': 20, 'tag': '...          3079197865   

                    source  possibly_sensitive  \
0       Twitter for iPhone               False   
1      Twitter for Android               False   
2       Twitter for iPhone               False   
3       Twitter for iPhone               False   
4       Twitter for iPhone               False   
...                    ...                 ...   
47939   Twitter for iPhone               False   
47940   Twitter for iPhone               False   
47941   Twitter for iPhone               False   
47942   Twitter for iPhone               False   
47943  Twitter for Android               False   

                                          public_metrics  ...  \
0      {'retweet_count': 0, 'reply_count': 0, 'like_c...  ...   
1      {'retweet_count': 0, 'reply_count': 0, 'like_c...  ...   
2      {'retweet_count': 0, 'reply_count': 0, 'like_c...  ...   
3      {'retweet_count': 9, 'reply_count': 1, 'like_c...  ...   
4      {'retweet_count': 0, 'reply_count': 0, 'like_c...  ...   
...                                                  ...  ...   
47939  {'retweet_count': 0, 'reply_count': 0, 'like_c...  ...   
47940  {'retweet_count': 0, 'reply_count': 1, 'like_c...  ...   
47941  {'retweet_count': 0, 'reply_count': 0, 'like_c...  ...   
47942  {'retweet_count': 0, 'reply_count': 0, 'like_c...  ...   
47943  {'retweet_count': 0, 'reply_count': 0, 'like_c...  ...   

                  full_name place_type              id_y country_code  \
0           Nacogdoches, TX       city  ebf78e870cecf

Heat Map for 7 days

In [76]:
#initialize the map and put the data into the map
map_7days_heatmap = folium.Map(location=[36.648693, -95.8974445],tiles="cartodbpositron", zoom_start=4) 

# List comprehension to make out list of lists
heat_data = [[[row['Latitude'],row['Lontitude']] for index, row in total_df[total_df['Day'] == i].iterrows()] for i in range(1,)]

# Plot it on the map
hm = HeatMapWithTime(heat_data,auto_play=True,max_opacity=0.8)
hm.add_to(map_7days_heatmap)

#show the heat map
map_7days_heatmap

Grid Heat Map for Each 7 days

In [78]:
#use a function to get which place grid box does the tweets belong to
def get_grid_identifier(df):
    x_index = 0
    y_index = 0
    
    x_step = (upper_right_coordinates[0]-lower_left_coordinates[0])/(m_box)
    y_step = (upper_right_coordinates[1]-lower_left_coordinates[1])/(n_box)
    
    while x_index < m_box:
        if lower_left_coordinates[0]+ (x_index+1)* x_step> df['Lontitude']:
            break
        x_index = x_index+1
    
        
    while y_index < n_box:
        if lower_left_coordinates[1]+ (y_index+1)* y_step> df['Latitude']:
            break
        y_index = y_index+1
        
    return str(x_index)+"x"+str(y_index)

tws_50_merge['identifier'] = tws_50_merge.apply(get_grid_identifier,axis = 1)
tws_51_merge['identifier'] = tws_51_merge.apply(get_grid_identifier,axis = 1)
tws_52_merge['identifier'] = tws_52_merge.apply(get_grid_identifier,axis = 1)
tws_53_merge['identifier'] = tws_53_merge.apply(get_grid_identifier,axis = 1)
tws_54_merge['identifier'] = tws_54_merge.apply(get_grid_identifier,axis = 1)
tws_55_merge['identifier'] = tws_55_merge.apply(get_grid_identifier,axis = 1)
tws_56_merge['identifier'] = tws_56_merge.apply(get_grid_identifier,axis = 1)


context_annotations  \
0     [{'domain': {'id': '123', 'name': 'Ongoing New...   
1     [{'domain': {'id': '123', 'name': 'Ongoing New...   
2     [{'domain': {'id': '123', 'name': 'Ongoing New...   
3     [{'domain': {'id': '123', 'name': 'Ongoing New...   
4     [{'domain': {'id': '123', 'name': 'Ongoing New...   
...                                                 ...   
5728  [{'domain': {'id': '10', 'name': 'Person', 'de...   
5729  [{'domain': {'id': '10', 'name': 'Person', 'de...   
5730  [{'domain': {'id': '3', 'name': 'TV Shows', 'd...   
5731  [{'domain': {'id': '123', 'name': 'Ongoing New...   
5732  [{'domain': {'id': '123', 'name': 'Ongoing New...   

                                                   text  \
0     Need to be jailed for that cut... https://t.co...   
1     @loydcase The infection rate is exponentially ...   
2     @tedcruz Now the democrats are trying to edit ...   
3     Pasadena identifies at least 5 coronavirus cas...   
4     Vitamin D appears to play role in COVID-19 mor...   
...                                                 ...   
5728  cyndi lauper disinfecting herself after huggin...   
5729  @Yamiche Good #COVID19 don’t care! @realDonald...   
5730  Here’s your tweet of the night.\n\nPossible tw...   
5731  Today's Seva Day is sponsored by the Minhas Fa...   
5732  Check any country’s current corona standing wi...   

                                      referenced_tweets  \
0     [{'type': 'quoted', 'id': '1258823714268987392'}]   
1     [{'type': 'replied_to', 'id': '125920039262307...   
2     [{'type': 'replied_to', 'id': '125952166828589...   
3                                                   NaN   
4                                                   NaN   
...                                                 ...   
5728                                                NaN   
5729  [{'type': 'replied_to', 'id': '125963131328131...   
5730                                                NaN   
5731                                                NaN   
5732                                                NaN   

                    created_at            author_id lang                 id_x  \
0     2020-05-10T04:38:56.000Z             75673041   en  1259342131455549440   
1     2020-05-10T12:40:56.000Z             48369844   en  1259463430228119555   
2     2020-05-10T21:32:11.000Z             22336302   en  1259597124838318081   
3     2020-05-10T04:39:18.000Z           1699793220   en  1259342225160523776   
4     2020-05-10T04:39:32.000Z           1699793220   en  1259342283918512129   
...                        ...                  ...  ...                  ...   
5728  2020-05-11T04:09:02.000Z           1315323775   en  1259696994160959489   
5729  2020-05-11T04:09:11.000Z             25398734   en  1259697035067797513   
5730  2020-05-11T04:10:11.000Z  1123445103769604097   en  1259697286009032709   
5731  2020-05-11T04:11:27.000Z            152321513   en  1259697604507688960   
5732  2020-05-11T04:11:48.000Z            626848165   en  1259697691065323520   

                   source                                     public_metrics  \
0      Twitter for iPhone  {'retweet_count': 0, 'reply_count': 0, 'like_c...   
1     Twitter for Android  {'retweet_count': 0, 'reply_count': 1, 'like_c...   
2      Twitter for iPhone  {'retweet_count': 0, 'reply_count': 0, 'like_c...   
3     Twitter for Android  {'retweet_count': 0, 'reply_count': 0, 'like_c...   
4     Twitter for Android  {'retweet_count': 0, 'reply_count': 0, 'like_c...   
...                   ...                                                ...   
5728   Twitter for iPhone  {'retweet_count': 0, 'reply_count': 0, 'like_c...   
5729   Twitter for iPhone  {'retweet_count': 0, 'reply_count': 0, 'like_c...   
5730   Twitter for iPhone  {'retweet_count': 0, 'reply_count': 0, 'like_c...   
5731   Twitter for iPhone  {'retweet_count': 1, 'reply_count': 1, 'like_c...   
5732   Twitter for iPhone  {'retweet_count': 0, 'reply_c

In [96]:
#function to generate an m*n grid geo json as one strig
def get_geojson_grid(upper_right, lower_left, m,n):
    
    geo_json = {"type": "FeatureCollection",
                "properties":{
                    "lower_left": lower_left,
                    "upper_right": upper_right, 
                    "x_size": m,
                    "y_size":n
                },
                "features":[]}


    lat_steps = np.linspace(lower_left[1], upper_right[1], n+1)
    lon_steps = np.linspace(lower_left[0], upper_right[0], m+1)

    lat_stride = lat_steps[1] - lat_steps[0]
    lon_stride = lon_steps[1] - lon_steps[0]
    
    #mark the index
    x = 0
    y = 0

    for lat in lat_steps[:-1]:
        x = 0
        for lon in lon_steps[:-1]:
            # Define dimensions of box in grid
            upper_left = [lon, lat + lat_stride]
            upper_right = [lon + lon_stride, lat + lat_stride]
            lower_right = [lon + lon_stride, lat]
            lower_left = [lon, lat]
            
            #define the identifier name for it
            identity = str(x)+"x"+str(y)

            # Define json coordinates for polygon
            coordinates = [
                upper_left,
                upper_right,
                lower_right,
                lower_left,
                upper_left
            ]

            grid_feature = {
                "type":"Feature",
                "properties":{
                    "x_index":x,
                    "y_index":y,
                    "identifier": identity
                },
                "geometry":{
                    "type":"Polygon",
                    "coordinates": [coordinates],
                }
            }
            
            geo_json['features'].append(grid_feature)

            x = x + 1
        y = y+1

    return geo_json

#create the geojson of the grid
grid = get_geojson_grid(upper_right_coordinates, lower_left_coordinates , m_box,n_box)

In [100]:
# The grind map for 1
grind_data_50 = pd.DataFrame(tws_50_merge['identifier'].value_counts())
grind_data_50.reset_index(inplace=True)
grind_data_50.rename(columns={'identifier':'Count'},inplace=True)
grind_data_50['Day'] = 1

map_grid_50= folium.Map(location=[36.648693, -95.8974445],tiles="cartodbpositron", zoom_start=4)

#create the choropleth 
folium.Choropleth(
    geo_data=grid,
    data=grind_data_50,
    columns=['index','Count'],
    key_on='feature.properties.identifier',
    fill_color='YlOrRd',
    fill_opacity=0.8,
    line_opacity=0.2,
    highlight=True,
    legend_name='The number of tweets in the area'
).add_to(map_grid_50)

map_grid_50






In [102]:
# The grind map for 2
grind_data_51 = pd.DataFrame(tws_51_merge['identifier'].value_counts())
grind_data_51.reset_index(inplace=True)
grind_data_51.rename(columns={'identifier':'Count'},inplace=True)
grind_data_51['Day'] = 2
grind_data_51

map_grid_51= folium.Map(location=[36.648693, -95.8974445],tiles="cartodbpositron", zoom_start=4)

#create the choropleth 
folium.Choropleth(
    geo_data=grid,
    data=grind_data_51,
    columns=['index','Count'],
    key_on='feature.properties.identifier',
    fill_color='YlOrRd',
    fill_opacity=0.8,
    line_opacity=0.2,
    highlight=True,
    legend_name='The number of tweets in the area'
).add_to(map_grid_51)

map_grid_51

In [120]:
# The grind map for 3
grind_data_52 = pd.DataFrame(tws_52_merge['identifier'].value_counts())
grind_data_52.reset_index(inplace=True)
grind_data_52.rename(columns={'identifier':'Count'},inplace=True)
grind_data_52['Day'] = 3

map_grid_52= folium.Map(location=[36.648693, -95.8974445],tiles="cartodbpositron", zoom_start=4)

#create the choropleth 
folium.Choropleth(
    geo_data=grid,
    data=grind_data_52,
    columns=['index','Count'],
    key_on='feature.properties.identifier',
    fill_color='YlOrRd',
    fill_opacity=0.8,
    line_opacity=0.2,
    highlight=True,
    legend_name='The number of tweets in the area'
).add_to(map_grid_52)

map_grid_52


In [86]:
# The grind map for 4
grind_data_53 = pd.DataFrame(tws_53_merge['identifier'].value_counts())
grind_data_53.reset_index(inplace=True)
grind_data_53.rename(columns={'identifier':'Count'},inplace=True)
grind_data_53['Day'] = 4

map_grid_53= folium.Map(location=[36.648693, -95.8974445],tiles="cartodbpositron", zoom_start=4)

#create the choropleth 
folium.Choropleth(
    geo_data=grid,
    data=grind_data_53,
    columns=['index','Count'],
    key_on='feature.properties.identifier',
    fill_color='YlOrRd',
    fill_opacity=0.8,
    line_opacity=0.2,
    highlight=True,
    legend_name='The number of tweets in the area'
).add_to(map_grid_53)

map_grid_53

In [104]:
# The grind map for 5
grind_data_54 = pd.DataFrame(tws_54_merge['identifier'].value_counts())
grind_data_54.reset_index(inplace=True)
grind_data_54.rename(columns={'identifier':'Count'},inplace=True)
grind_data_54['Day'] = 5
grind_data_54

map_grid_54= folium.Map(location=[36.648693, -95.8974445],tiles="cartodbpositron", zoom_start=4)

#create the choropleth 
folium.Choropleth(
    geo_data=grid,
    data=grind_data_54,
    columns=['index','Count'],
    key_on='feature.properties.identifier',
    fill_color='YlOrRd',
    fill_opacity=0.8,
    line_opacity=0.2,
    highlight=True,
    legend_name='The number of tweets in the area'
).add_to(map_grid_54)

map_grid_54

In [105]:
# The grind map for 6
grind_data_55 = pd.DataFrame(tws_55_merge['identifier'].value_counts())
grind_data_55.reset_index(inplace=True)
grind_data_55.rename(columns={'identifier':'Count'},inplace=True)
grind_data_55['Day'] = 6

map_grid_55= folium.Map(location=[36.648693, -95.8974445],tiles="cartodbpositron", zoom_start=4)

#create the choropleth 
folium.Choropleth(
    geo_data=grid,
    data=grind_data_51,
    columns=['index','Count'],
    key_on='feature.properties.identifier',
    fill_color='YlOrRd',
    fill_opacity=0.8,
    line_opacity=0.2,
    highlight=True,
    legend_name='The number of tweets in the area'
).add_to(map_grid_55)

map_grid_55

In [106]:
# The grind map for 7
grind_data_56 = pd.DataFrame(tws_56_merge['identifier'].value_counts())
grind_data_56.reset_index(inplace=True)
grind_data_56.rename(columns={'identifier':'Count'},inplace=True)
grind_data_56['Day'] = 7

map_grid_56= folium.Map(location=[36.648693, -95.8974445],tiles="cartodbpositron", zoom_start=4)

#create the choropleth 
folium.Choropleth(
    geo_data=grid,
    data=grind_data_56,
    columns=['index','Count'],
    key_on='feature.properties.identifier',
    fill_color='YlOrRd',
    fill_opacity=0.8,
    line_opacity=0.2,
    highlight=True,
    legend_name='The number of tweets in the area'
).add_to(map_grid_56)

map_grid_56

Attempt for a grid map with time slider

In [125]:
total_grid_data =  pd.concat([grind_data_50, grind_data_51,grind_data_52,grind_data_53,grind_data_54,grind_data_55,grind_data_56])
total_grid_data.reset_index()
max_color = max(total_grid_data['Count'])
min_color = min(total_grid_data['Count'])
max_opacity, min_opacity = 1, 1
cmap = linear.YlGnBu_09.scale(min_color, max_color)

def norm(x):
    return (x - x.min()) / (x.max() - x.min())

